In [1]:
import pandas as pd
import numpy as np
import altair as alt
import sklearn.decomposition
import sklearn.cluster
import matplotlib.pyplot as pl
import scipy.stats
import mca

In [2]:
antworten = pd.read_excel('Antworten.ods')
antworten['Aussage'] = [x.strip() for x in antworten['Aussage']]
antworten.index = antworten['Aussage']
del antworten['Aussage']
antworten -= 2
antworten.head()

CDU/CSU  SPD  AfD  FDP  \
Aussage                                                                      
Auf allen Autobahnen soll ein generelles Tempol...       -1    1   -1   -1   
Deutschland soll seine Verteidigungsausgaben er...        1    1    1    1   
Bei Bundestagswahlen sollen auch Jugendliche ab...       -1    1   -1    1   
Die Förderung von Windenergie soll beendet werden.       -1   -1    1    0   
Die Möglichkeiten der Vermieterinnen und Vermie...        0    1   -1   -1   

                                                    LINKE  GRÜNE  \
Aussage                                                            
Auf allen Autobahnen soll ein generelles Tempol...      1      1   
Deutschland soll seine Verteidigungsausgaben er...     -1     -1   
Bei Bundestagswahlen sollen auch Jugendliche ab...      1      1   
Die Förderung von Windenergie soll beendet werden.     -1     -1   
Die Möglichkeiten der Vermieterinnen und Vermie...      1      1   

                                                    FREIE WÄHLER  Die PARTEI  \
Aussage                                                                        
Auf allen Autobahnen soll ein generelles Tempol...            -1           1   
Deutschland soll seine Verteidigungsausgaben er...             1          -1   
Bei Bundestagswahlen sollen auch Jugendliche ab...            -1           1   
Die Förderung von Windenergie soll beendet werden.            -1          -1   
Die Möglichkeiten der Vermieterinnen und Vermie...            -1           1   

                                                    Tierschutzpartei  NPD  \
Aussage                                                                     
Auf allen Autobahnen soll ein generelles Tempol...                 1   -1   
Deutschland soll seine Verteidigungsausgaben er...                -1    1   
Bei Bundestagswahlen sollen auch Jugendliche ab...                 1   -1   
Die Förderung von Windenergie soll beendet werden.                -1    1   
Die Möglichkeiten der Vermieterinnen und Vermie...                 1    0   

                                                    ...  Der 3. Weg  \
Aussage                                             ...               
Auf allen Autobahnen soll ein generelles Tempol...  ...           0   
Deutschland soll seine Verteidigungsausgaben er...  ...           1   
Bei Bundestagswahlen sollen auch Jugendliche ab...  ...          -1   
Die Förderung von Windenergie soll beendet werden.  ...           1   
Die Möglichkeiten der Vermieterinnen und Vermie...  ...           1   

                                                    Bündnis 21  \
Aussage                                                          
Auf allen Autobahnen soll ein generelles Tempol...          -1   
Deutschland soll seine Verteidigungsausgaben er...          -1   
Bei Bundestagswahlen sollen auch Jugendliche ab...          -1   
Die Förderung von Windenergie soll beendet werden.           1   
Die Möglichkeiten der Vermieterinnen und Vermie...          -1   

                                                    Europäische Partei LIEBE  \
Aussage                                                                        
Auf allen Autobahnen soll ein generelles Tempol...                         1   
Deutschland soll seine Verteidigungsausgaben er...                         1   
Bei Bundestagswahlen sollen auch Jugendliche ab...                         1   
Die Förderung von Windenergie soll beendet werden.                         1   
Die Möglichkeiten der Vermieterinnen und Vermie...                         1   

                                                    Liberal-Konservative Reformer  \
Aussage                                                                             
Auf allen Autobahnen soll ein generelles Tempol...                             -1   
Deutschland soll seine Verteidigungsausgaben er...                              1   
Bei Bundestagswahlen sollen auch Jugendliche ab...               

In [14]:
anzahl_parteien = len(antworten.columns)
anzahl_fragen = len(antworten)

In [15]:
p = scipy.stats.spearmanr(antworten.T)
df = pd.DataFrame(p.correlation)
df.index = antworten.index
df.columns = antworten.index
long = df.melt(ignore_index=False)
long.index.name = 'Aussage 1'
long.columns = ['Aussage 2', 'Korrelation']
long = long.reset_index()

chart = (
    alt.Chart(
        long,
        title='Korrelation der Fragen'
    )
    .mark_rect()
    .encode(
        alt.X('Aussage 1'),
        alt.Y('Aussage 2'),
        alt.Fill('Korrelation', scale=alt.Scale(scheme='pinkyellowgreen', domain=(-1, 1))),
        [alt.Tooltip('Aussage 1'),
        alt.Tooltip('Aussage 2'),
        alt.Tooltip('Korrelation')],
    )
)
chart.save('korrelation_fragen.json')
chart

alt.Chart(...)

In [16]:
p = scipy.stats.spearmanr(antworten)
df = pd.DataFrame(p.correlation)
df.index = antworten.columns
df.columns = antworten.columns
long = df.melt(ignore_index=False)
long.index.name = 'Partei 1'
long.columns = ['Partei 2', 'Korrelation']
long = long.reset_index()

chart = (
    alt.Chart(
        long,
        title='Korrelation der Parteien'
    )
    .mark_rect()
    .encode(
        alt.X('Partei 1'),
        alt.Y('Partei 2'),
        alt.Fill('Korrelation', scale=alt.Scale(scheme='pinkyellowgreen', domain=(-1, 1))),
        [alt.Tooltip('Partei 1'),
        alt.Tooltip('Partei 2'),
        alt.Tooltip('Korrelation')],
    )
)
chart.save('korrelation_parteien.json')
chart

/usr/lib64/python3.9/site-packages/numpy/lib/function_base.py:2642: RuntimeWarning: invalid value encountered in true_divide
  c /= stddev[:, None]
/usr/lib64/python3.9/site-packages/numpy/lib/function_base.py:2643: RuntimeWarning: invalid value encountered in true_divide
  c /= stddev[None, :]


alt.Chart(...)

In [17]:
pca = sklearn.decomposition.PCA(2)
reduced = pca.fit_transform(antworten.T)

In [18]:
pca_df = pd.DataFrame({
    'Partei': antworten.columns,
    'Komponente 1': reduced[:, 0],
    'Komponente 2': reduced[:, 1],
})
pca_df.head()

Partei  Komponente 1  Komponente 2
0  CDU/CSU      4.176082      2.695897
1      SPD     -1.516500      1.301237
2      AfD      5.970159      0.196338
3      FDP      2.455794      4.145112
4    LINKE     -4.361681     -0.859561

In [19]:
chart = (
    alt.Chart(
        pca_df,
        title='PCA der Positionen',
        width=600,
        height=400,
    )
    .mark_text()
    .encode(
        alt.X('Komponente 1'),
        alt.Y('Komponente 2'),
        alt.Text('Partei'),
    )
    .interactive()
)
chart.save('parteien_pca2.json')
chart

alt.Chart(...)

In [20]:
hauptachsen = pd.DataFrame({
    'Frage': antworten.index,
    'Gewicht 1': pca.components_[0],
    'Gewicht 2': pca.components_[1],
})
hauptachsen.head()

Frage  Gewicht 1  Gewicht 2
0  Auf allen Autobahnen soll ein generelles Tempo...  -0.219745  -0.080291
1  Deutschland soll seine Verteidigungsausgaben e...   0.220536   0.099520
2  Bei Bundestagswahlen sollen auch Jugendliche a...  -0.258164   0.126626
3  Die Förderung von Windenergie soll beendet wer...   0.203038  -0.207529
4  Die Möglichkeiten der Vermieterinnen und Vermi...  -0.184809  -0.206166

In [21]:
chart = (
    alt.Chart(
        hauptachsen,
        title='Hauptachse 1',
       
    )
    .mark_bar()
    .encode(
        alt.X('Gewicht 1'),
        alt.Y('Frage', sort='-x'),
        alt.Tooltip('Frage')
    )
)
chart.save('hauptachse_1_fragen.json')
chart

alt.Chart(...)

In [22]:
chart = (
    alt.Chart(
        hauptachsen,
        title='Hauptachse 2',
       
    )
    .mark_bar()
    .encode(
        alt.X('Gewicht 2'),
        alt.Y('Frage', sort='-x'),
        alt.Tooltip('Frage')
    )
)
chart.save('hauptachse_2_fragen.json')
chart

alt.Chart(...)

In [30]:
for k in [2, 3, 4, 5, 10]:
    k_means = sklearn.cluster.KMeans(n_clusters=k, random_state=0).fit(antworten.T)
    parteien_df = pd.DataFrame({
        'Name': antworten.columns,
        'Cluster': k_means.labels_
    }).set_index('Name')

    for key, values in parteien_df.groupby('Cluster').groups.items():
        print('-', ', '.join(sorted(values, key=lambda x: x.lower())))
    print()

- Demokratie in Bewegung, Deutsche Kommunistische Partei, Die Humanisten, Die PARTEI, Die Urbane, GRÜNE, LINKE, Lobbyisten für Kinder, Marxistisch-Leninistische Partei Deutschlands, Partei für Veränderung, Vegetarier und Veganer, PIRATEN, Sozialistische Gleichheitspartei, SPD, Südschleswiger Wählerverband, Tierschutzallianz, Tierschutzpartei, Volt, Ökologisch-Demokratische Partei
- AfD, Bayernpartei, Bündnis 21, Bündnis C  - Christen für Deutschland, Bürgerbewegung für Fortschritt und Wandel, Bürgerrechtsbewegung Solidarität, CDU/CSU, Der 3. Weg, Die Grauen, dieBasis, Europäische Partei LIEBE, FDP, FREIE WÄHLER, Gesundheitsforschung, Liberal-Konservative Reformer, Menschliche Welt, NPD, Partei des Fortschritts, Team Todenhöfer, Unabhängige für bürgernahe Demokratie

- Demokratie in Bewegung, Deutsche Kommunistische Partei, Die Humanisten, Die PARTEI, Die Urbane, GRÜNE, LINKE, Lobbyisten für Kinder, Marxistisch-Leninistische Partei Deutschlands, Partei des Fortschritts, Partei für Verän

In [24]:
pca = sklearn.decomposition.PCA(2)
reduced = pca.fit_transform(antworten)

pca_df = pd.DataFrame({
    'Frage': antworten.index,
    'Komponente 1': reduced[:, 0],
    'Komponente 2': reduced[:, 1],
})
pca_df.head()

chart = (
    alt.Chart(
        pca_df,
        title='PCA der Fragen',
        width=600,
        height=400,
    )
    .mark_circle()
    .encode(
        alt.X('Komponente 1'),
        alt.Y('Komponente 2'),
        alt.Tooltip('Frage'),
    )
    .interactive()
)
chart.save('fragen_pca2.json')
chart

alt.Chart(...)

In [25]:
hauptachsen = pd.DataFrame({
    'Frage': antworten.columns,
    'Gewicht 1': pca.components_[0],
    'Gewicht 2': pca.components_[1],
})
hauptachsen.head()

Frage  Gewicht 1  Gewicht 2
0  CDU/CSU   0.133425  -0.111516
1      SPD  -0.137705  -0.066150
2      AfD   0.208581  -0.211449
3      FDP   0.062387  -0.061424
4    LINKE  -0.273793   0.029210

In [26]:
chart = (
    alt.Chart(
        hauptachsen,
        title='Hauptachse 1',
       
    )
    .mark_bar()
    .encode(
        alt.X('Gewicht 1'),
        alt.Y('Frage', sort='-x'),
        alt.Tooltip('Frage')
    )
)
chart.save('hauptachse_1_parteien.json')
chart

alt.Chart(...)

In [27]:
chart = (
    alt.Chart(
        hauptachsen,
        title='Hauptachse 2',
       
    )
    .mark_bar()
    .encode(
        alt.X('Gewicht 2'),
        alt.Y('Frage', sort='-x'),
        alt.Tooltip('Frage')
    )
)
chart.save('hauptachse_2_parteien.json')
chart

alt.Chart(...)

In [28]:
k_means = sklearn.cluster.KMeans(n_clusters=5, random_state=0).fit(antworten)
parteien_df = pd.DataFrame({
    'Name': antworten.index,
    'Cluster': k_means.labels_
}).set_index('Name')

for key, values in parteien_df.groupby('Cluster').groups.items():
    print('1.')
    print()
    for frage in sorted(values):
        print('    -', frage)
    print()

1.

    - Auch Ehepaare ohne Kinder sollen weiterhin steuerlich begünstigt werden.
    - Der Staat soll weiterhin für Religionsgemeinschaften die Kirchensteuer einziehen.
    - Impfstoffe gegen Covid-19 sollen weiterhin durch Patente geschützt sein.
    - Spenden von Unternehmen an Parteien sollen weiterhin erlaubt sein.

1.

    - Auf allen Autobahnen soll ein generelles Tempolimit gelten.
    - Bei Bundestagswahlen sollen auch Jugendliche ab 16 Jahren wählen dürfen.
    - Bundesbehörden sollen in ihren Veröffentlichungen unterschiedliche Ge schlechtsidentitäten sprachlich berücksichtigen.
    - Das Tragen eines Kopftuchs soll Beamtinnen im Dienst generell erlaubt sein.
    - Der Bund soll Projekte zur Bekämpfung des Antisemitismus stärker finanziell unterstützen.
    - Der für das Jahr 2038 geplante Ausstieg aus der Kohleverstromung soll vorgezogen werden.
    - Der kontrollierte Verkauf von Cannabis soll generell erlaubt sein.
    - Der staatlich festgelegte Preis für den Ausstoß vo

In [111]:
antworten2 = antworten.drop("Gesundheitsforschung", axis=1)

mca_df = mca.MCA(antworten2.T + 2)

df = pd.DataFrame({'Partei': antworten2.columns, 'fs_r': mca_df.fs_r(1.0).flatten()})

chart = (
    alt.Chart(
        df
    )
    .mark_bar()
    .encode(
        alt.X('fs_r'),
        alt.Y('Partei', sort='-x'),
    )
)
chart.save('mca_parteien.json')
chart

alt.Chart(...)

In [109]:
mca_df = mca.MCA(antworten + 2)
df = pd.DataFrame({'Frage': antworten.index, 'fs_r': mca_df.fs_r(0.1).flatten()})

chart = (
    alt.Chart(
        df
    )
    .mark_bar()
    .encode(
        alt.X('fs_r'),
        alt.Y('Frage', sort='-x'),
        alt.Tooltip('Frage'),
    )
)
chart.save('mca_fragen.json')
chart

alt.Chart(...)

In [4]:
pca_df = pd.DataFrame({
    'Frage': antworten.index,
    'Komponente 1': reduced[:, 0],
    'Komponente 2': reduced[:, 1],
})
pca_df.head()

chart = (
    alt.Chart(
        pca_df,
        title='PCA der Fragen',
        width=600,
        height=400,
    )
    .mark_circle()
    .encode(
        alt.X('Komponente 1'),
        alt.Y('Komponente 2'),
        alt.Tooltip('Frage'),
    )
    .interactive()
)
chart.save('fragen_pca2.json')
chart

LinAlgError: SVD did not converge